In [ ]:
import transformers
import torch
import datasets  
import json  
from tqdm import tqdm
device = "cuda"

# Load the tokenizer and model
tokenizer = transformers.AutoTokenizer.from_pretrained("/mnt/lingjiejiang/textual_aesthetics/exp/saves/bitnet_glan2_2048_default_template/fullft_lr2e5_4kstep/sft/checkpoint-3000", trust_remote_code=True)
model = transformers.AutoModelForCausalLM.from_pretrained("/mnt/lingjiejiang/textual_aesthetics/exp/saves/bitnet_glan2_2048_default_template/fullft_lr2e5_4kstep/sft/checkpoint-3000", trust_remote_code=True, torch_dtype=torch.bfloat16, attn_implementation = "flash_attention_2").eval()
model.to(device)

  
gen_kwargs_hf = {  
    "max_new_tokens": 2048,  
    "temperature": 0.3,  
    "do_sample": True,
    "top_p": 0.9,
    "top_k": 50,
}  
  
gen_kwargs_hf['eos_token_id'] = [tokenizer.eos_token_id, tokenizer.convert_tokens_to_ids("<|end_of_text|>")]
gen_kwargs_hf['pad_token_id'] = tokenizer.eos_token_id 

def generate_response(prompt):  
    # print(f"prompt: {prompt}")
    inputs = tokenizer(prompt, return_tensors="pt", add_special_tokens=False).to(model.device)  
    # print(f"inputs:{inputs}")
    tokens = model.generate(**inputs, **gen_kwargs_hf)  
    res = tokenizer.decode(tokens[0], skip_special_tokens=True)
    # print(res)
    return tokenizer.decode(tokens[0], skip_special_tokens=True).replace(prompt, '')  
  
# Load dataset  
eval_set = datasets.load_dataset("tatsu-lab/alpaca_eval", "alpaca_eval")["eval"]  
  
# Convert dataset examples to messages  
def convert_to_message(example):  
    messages = [{"role": "user", "content": example["instruction"]}]  
    example["messages"] = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)  
    return example  
  
eval_set = eval_set.map(convert_to_message)  
  
# Generate responses  
outputs_text = []  
idx = 0
for example in tqdm(eval_set):  
    idx += 1
    if idx == 1:
        continue

    response = generate_response(example['messages'])  
    print(response)
    outputs_text.append(response)  

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

  0%|          | 2/805 [02:52<19:15:51, 86.37s/it]

Human: How did US states get their names?
Assistant:The names of US states were originally given by Native Americans. For example, the state of New York was named after the Mohawk tribe. The state of Virginia was named after the Virginia Company, which was a group of English investors who settled in the area. The state of North Carolina was named after the English nobleman, Lord, who was the first governor of the colony. The state of South Carolina was named after the English king, Charles, who was the first governor of the colony. The state of Georgia was named after the English king, George, who was the first governor of the colony. The state of Tennessee was named after the English king, Henry, who was the first governor of the colony. The state of Alabama was named after the English king, Alfred, who was the first governor of the colony. The state of Mississippi was named after the English king, Henry, who was the first governor of the colony. The state of Florida was named after t

  0%|          | 3/805 [05:24<25:19:51, 113.71s/it]

Human: Hi, my sister and her girlfriends want me to play kickball with them. Can you explain how the game is played, so they don't take advantage of me?
Assistant:Sure! Kickball is a fun game that involves kicking a ball to score points. Here's a step-by-step guide to help you understand how to play kickball:

### Step 1: Gather Your Equipment
You'll need a ball and a field to play on. A soccer ball is commonly used, but you can also use a tennis ball or even a softball.

### Step 2: Understand the Field
The field is divided into two halves. The goal is to score points by kicking the ball into the opposing team's half. The field is marked by lines and boundaries.

### Step 3: Learn the Rules
Kickball is a simple game with the following rules:

1. **Objective**: Score points by kicking the ball into the opponent's half.
2. **Scoring**: Points are scored when the ball is kicked into the opponent's half.
3. **Game Duration**: The game is played for a fixed number of minutes, usually 60 mi

...

Human: What is the james webb telescope
Assistant:The James Webb Telescope (JWST) is a space-based telescope designed to observe the earliest stages of the universe. It is named after James Webb, an American astronomer who played a significant role in the development of the telescope. The JWST is currently being built and launched in 2021, and it is expected to provide unprecedented insights into the early stages of the universe.


 51%|█████     | 409/805 [6:24:01<2:34:15, 23.37s/it]

Human: can you write code?
Assistant:Sure, I'd be happy to help! Please provide the code you'd like to write, and I can assist you in creating it.


 51%|█████     | 410/805 [6:26:19<6:20:29, 57.80s/it]

Human: What are the lyrics to the third verse of Rick Astley's Never Gonna Give You Up?
Assistant:The lyrics to the third verse of Rick Astley's Never Gonna Give You Up are:

"Never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up, never gonna give you up,

In [10]:
from openai import OpenAI
# Set OpenAI's API key and API base to use vLLM's API server.
openai_api_key = "EMPTY"
openai_api_base = "http://localhost:8000/v1"

client = OpenAI(
    api_key=openai_api_key,
    base_url=openai_api_base,
)

chat_response = client.chat.completions.create(
    model="/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/Meta-Llama-3.1-8B-Instruct",
    messages=[
        {"role": "system", "content": "You are a helpful assistant."},
        {"role": "user", "content": "write pcre regex for not containing  C:"},
    ],
    temperature=0,
    max_tokens=2048
)
# print("Chat response:", chat_response)
print(f"res:{chat_response.choices[0].message.content}")
res1 = chat_response.choices[0].message.content

res:To match a string that does not contain 'C:', you can use a negative lookahead assertion in PCRE regex. Here's how you can do it:

```regex
^(?!.*C:).*
```

Explanation:

- `^` asserts the start of the line.
- `(?!` starts a negative lookahead assertion.
- `.*` matches any character (except newline) 0 or more times.
- `C:` is the string we want to avoid.
- `)` ends the negative lookahead assertion.
- `.*` matches any character (except newline) 0 or more times, allowing the regex to match the rest of the string.

However, if you want to match a string that does not contain 'C:' anywhere in the string, not just at the start, you can use the following regex:

```regex
^(?!.*C:).*
```

This will match any string that does not contain 'C:' anywhere in it.

If you want to match a string that does not contain 'C:' at the start, you can use the following regex:

```regex
^(?!C:).*
```

This will match any string that does not start with 'C:'.

Here are some examples in PHP:

```php
$patter

In [1]:
from vllm import LLM, SamplingParams
from tqdm import tqdm
# import datasets
template = "{{ '<|begin_of_text|>' }}{% if messages[0]['role'] == 'system' %}{% set system_message = messages[0]['content'] %}{% endif %}{% if system_message is defined %}{{ '<|start_header_id|>system<|end_header_id|>\n\n' + system_message + '<|eot_id|>' }}{% endif %}{% for message in messages %}{% set content = message['content'] %}{% if message['role'] == 'user' %}{{ '<|start_header_id|>user<|end_header_id|>\n\n' + content + '<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\n' }}{% elif message['role'] == 'assistant' %}{{ content + '<|eot_id|>' }}{% endif %}{% endfor %}"

sampling_params = SamplingParams(temperature=0, max_tokens=2048)
# model_name = "Meta-Llama-3.1-8B"
model_name = "Meta-Llama-3.1-8B-Instruct"
# Create an LLM.
llm = LLM(model=f"/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/{model_name}", dtype="float32")

tokenizer = llm.get_tokenizer()
# tokenizer.chat_template = template
if tokenizer.chat_template is None:
    tokenizer.chat_template = template
    print("tokenizer is None, use setted template")
else:
    print("use original template")

/home/v-lingjiang/miniconda3/envs/eval/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-09-20 17:00:17,438	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 09-20 17:00:20 config.py:1446] Upcasting torch.bfloat16 to torch.float32.
WARNING 09-20 17:00:20 arg_utils.py:766] Chunked prefill is enabled by default for models with max_model_len > 32K. Currently, chunked prefill might not work with some features or models. If you encounter any issues, please disable chunked prefill by setting --enable-chunked-prefill=False.
INFO 09-20 17:00:20 config.py:820] Chunked prefill is enabled with max_num_batched_tokens=512.
INFO 09-20 17:00:20 llm_engine.py:174] Initializing an LLM engine (v0.5.4) with config: model='/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/Meta-Llama-3.1-8B-Instruct', speculative_config=None, tokenizer='/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/Meta-Llama-3.1-8B-Instruct', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, rope_scaling=None, rope_theta=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float32, max_seq_len=131072, down

/home/v-lingjiang/miniconda3/envs/eval/lib/python3.10/site-packages/xformers/ops/fmha/flash.py:211: FutureWarning: `torch.library.impl_abstract` was renamed to `torch.library.register_fake`. Please use that instead; we will remove `torch.library.impl_abstract` in a future version of PyTorch.
  @torch.library.impl_abstract("xformers_flash::flash_fwd")
/home/v-lingjiang/miniconda3/envs/eval/lib/python3.10/site-packages/xformers/ops/fmha/flash.py:344: FutureWarning: `torch.library.impl_abstract` was renamed to `torch.library.register_fake`. Please use that instead; we will remove `torch.library.impl_abstract` in a future version of PyTorch.
  @torch.library.impl_abstract("xformers_flash::flash_bwd")


INFO 09-20 17:00:29 model_runner.py:720] Starting to load model /mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/Meta-Llama-3.1-8B-Instruct...
INFO 09-20 17:00:29 selector.py:156] Cannot use FlashAttention-2 backend for dtype other than torch.float16 or torch.bfloat16.
INFO 09-20 17:00:29 selector.py:54] Using XFormers backend.


Loading safetensors checkpoint shards:   0% Completed | 0/4 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  25% Completed | 1/4 [00:06<00:19,  6.65s/it]
Loading safetensors checkpoint shards:  50% Completed | 2/4 [00:13<00:13,  6.91s/it]
Loading safetensors checkpoint shards:  75% Completed | 3/4 [00:20<00:06,  6.83s/it]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:24<00:00,  5.70s/it]
Loading safetensors checkpoint shards: 100% Completed | 4/4 [00:24<00:00,  6.11s/it]


INFO 09-20 17:00:54 model_runner.py:732] Loading model weights took 29.9776 GB


INFO 09-20 17:00:57 gpu_executor.py:102] # GPU blocks: 10162, # CPU blocks: 1024
INFO 09-20 17:01:00 model_runner.py:1024] Capturing the model for CUDA graphs. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 09-20 17:01:00 model_runner.py:1028] CUDA graphs can take additional 1~3 GiB memory per GPU. If you are running out of memory, consider decreasing `gpu_memory_utilization` or enforcing eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INFO 09-20 17:01:19 model_runner.py:1225] Graph capturing finished in 19 secs.
use original template


In [23]:
from transformers import AutoTokenizer  
from vllm import LLM, SamplingParams  
  
# # 加载分词器和模型  
# model_path = "/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/Meta-Llama-3.1-8B-Instruct"  
# tokenizer = AutoTokenizer.from_pretrained(model_path)  
# llm = LLM(model_path)  
  
# 定义生成参数  
gen_kwargs_vllm = {  
    "max_tokens": 2048,  
    "temperature": 0,  
    "repetition_penalty": 1.0,  
}  
gen_kwargs_vllm['stop_token_ids'] = [tokenizer.eos_token_id, tokenizer.convert_tokens_to_ids("<|end_of_text|>")]  
sampling_params = SamplingParams(**gen_kwargs_vllm)  
  
# 定义消息  
messages1 = [  
    {"role": "system", "content": "You are a helpful assistant."},  
    {"role": "user", "content": "write pcre regex for not containing  C:"},  
]  
messages2 = [  
    {"role": "system", "content": "You are a helpful assistant."},  
    {"role": "user", "content": "Proof that Q(sqrt(-11)) is a principal ideal domain"},  
]  
messages3 = [  
    {"role": "system", "content": "You are a helpful assistant."},  
    {"role": "user", "content": "What is the most successful go to market strategy for a managed services business?"},  
]  
messages4 = [  
    {"role": "system", "content": "You are a helpful assistant."},  
    {"role": "user", "content": "show me the steps to build an invoice app using phython"},  
]  
messages5 = [  
    {"role": "system", "content": "You are a helpful assistant."},  
    {"role": "user", "content": "give me JavaScript code to calculate pi"},  
]  
# messages = [messages1, messages2, messages3, messages4, messages5]  
messages = [messages1, messages2, messages3, messages4]  
# messages = [messages1]  
# 创建prompt  
input_prompts = [tokenizer.apply_chat_template(item, tokenize=False, add_generation_prompt=True) for item in messages]  
# input_ids = [tokenizer.encode(x, add_special_tokens=False) for x in input_prompts]
# 使用batch_encode_plus进行批量编码  
encoded_inputs = tokenizer.batch_encode_plus(  
    input_prompts,  
    add_special_tokens=False,
    # padding=True,  # 自动添加padding  
    # truncation=True,  # 如果需要可以截断  
    # return_tensors='pt'  # 返回PyTorch的张量  
)  
  
# 获取编码后的输入ID  
input_ids = encoded_inputs['input_ids']  
# input_ids = encoded_inputs["input_ids"]
  
# 进行生成  
res = llm.generate(prompt_token_ids=input_ids, sampling_params=sampling_params)  
  
# 打印结果  
for i, output in enumerate(res):  
    print(f"Result {i + 1}: {output.outputs[0].text}")  


Processed prompts: 100%|██████████| 4/4 [00:34<00:00,  8.61s/it, est. speed input: 6.18 toks/s, output: 95.08 toks/s]

Result 1: To match a string that does not contain 'C:', you can use a negative lookahead assertion in PCRE regex. Here's how you can do it:

```regex
^(?!.*C:).*$
```

Explanation:

- `^` asserts the start of the line.
- `(?!.*C:)` is a negative lookahead assertion that checks if the string does not contain 'C:' anywhere. 
  - `.*` matches any character (except newline) 0 or more times.
  - `C:` matches the string 'C:' literally.
- `.*` matches any character (except newline) 0 or more times.
- `$` asserts the end of the line.

This regex will match any string that does not contain 'C:'.

Example use case in PHP:

```php
$pattern = '/^(?!.*C:).*$/';
$string = 'This is a test string without C:';
if (preg_match($pattern, $string)) {
    echo "The string does not contain 'C:'";
} else {
    echo "The string contains 'C:'";
}
```

This will output: "The string does not contain 'C:'"
Result 2: To prove that Q(sqrt(-11)) is a principal ideal domain, we need to show that every ideal in Q(sqrt(

In [24]:
res_text_4 = [item.outputs[0].text for item in res]

In [8]:
res_text_2 = [item.outputs[0].text for item in res]
res_text_2

['To match a string that does not contain \'C:\', you can use a negative lookahead assertion in PCRE regex. Here\'s how you can do it:\n\n```regex\n^(?!.*C:).*$\n```\n\nExplanation:\n\n- `^` asserts the start of the line.\n- `(?!.*C:)` is a negative lookahead assertion that checks if the string does not contain \'C:\' anywhere. \n  - `.*` matches any character (except newline) 0 or more times.\n  - `C:` matches the string \'C:\' literally.\n- `.*` matches any character (except newline) 0 or more times.\n- `$` asserts the end of the line.\n\nThis regex will match any string that does not contain \'C:\'.\n\nExample use case in PHP:\n\n```php\n$pattern = \'/^(?!.*C:).*$/\';\n$string = \'This is a test string without C:\';\nif (preg_match($pattern, $string)) {\n    echo "The string does not contain \'C:\'";\n} else {\n    echo "The string contains \'C:\'";\n}\n```\n\nThis will output: "The string does not contain \'C:\'"']

In [19]:
res_text_3 = [item.outputs[0].text for item in res]

In [22]:
res_text_1[0] == res_text_2[0]

True

In [30]:
for i in range(len(res_text_3)):
    print(f"{i} {res_text_1[i] == res_text_4[i]}")

0 True
1 True
2 True


In [10]:
res_text_2[0]

'To match a string that does not contain \'C:\', you can use a negative lookahead assertion in PCRE regex. Here\'s how you can do it:\n\n```regex\n^(?!.*C:).*$\n```\n\nExplanation:\n\n- `^` asserts the start of the line.\n- `(?!.*C:)` is a negative lookahead assertion that checks if the string does not contain \'C:\' anywhere. \n  - `.*` matches any character (except newline) 0 or more times.\n  - `C:` matches the string \'C:\' literally.\n- `.*` matches any character (except newline) 0 or more times.\n- `$` asserts the end of the line.\n\nThis regex will match any string that does not contain \'C:\'.\n\nExample use case in PHP:\n\n```php\n$pattern = \'/^(?!.*C:).*$/\';\n$string = \'This is a test string without C:\';\nif (preg_match($pattern, $string)) {\n    echo "The string does not contain \'C:\'";\n} else {\n    echo "The string contains \'C:\'";\n}\n```\n\nThis will output: "The string does not contain \'C:\'"'

In [9]:
res_text_2[0] == res_text_1[0]

True

In [6]:
res_text_1 = [item.outputs[0].text for item in res]
res_text_1

['To match a string that does not contain \'C:\', you can use a negative lookahead assertion in PCRE regex. Here\'s how you can do it:\n\n```regex\n^(?!.*C:).*$\n```\n\nExplanation:\n\n- `^` asserts the start of the line.\n- `(?!.*C:)` is a negative lookahead assertion that checks if the string does not contain \'C:\' anywhere. \n  - `.*` matches any character (except newline) 0 or more times.\n  - `C:` matches the string \'C:\' literally.\n- `.*` matches any character (except newline) 0 or more times.\n- `$` asserts the end of the line.\n\nThis regex will match any string that does not contain \'C:\'.\n\nExample use case in PHP:\n\n```php\n$pattern = \'/^(?!.*C:).*$/\';\n$string = \'This is a test string without C:\';\nif (preg_match($pattern, $string)) {\n    echo "The string does not contain \'C:\'";\n} else {\n    echo "The string contains \'C:\'";\n}\n```\n\nThis will output: "The string does not contain \'C:\'"',
 "To prove that Q(sqrt(-11)) is a principal ideal domain, we need t

In [1]:
from vllm import LLM, SamplingParams
from tqdm import tqdm
import datasets
import json
import argparse 

# parser = argparse.ArgumentParser(description='Set model name.')  
# parser.add_argument('--model-name', type=str, required=True, help='Name of the model to use')  
# parser.add_argument('--model-path', type=str, default="/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints", help='Dir of the model to use') 
# args = parser.parse_args()  
# path_dir = args.model_path
# model_name = args.model_name data/arena-hard-v0.1/model_answer/.jsonl
path_dir = "/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/tulu_v2_8b_default_template_dpo_list_bsz1_trible_debug_v14"
model_name = "Meta-Llama-3.1-8B-Instruct"
# template = "{{ '<|begin_of_text|>' }}{% if messages[0]['role'] == 'system' %}{% set system_message = messages[0]['content'] %}{% endif %}{% if system_message is defined %}{{ '<|start_header_id|>system<|end_header_id|>\n\n' + system_message + '<|eot_id|>' }}{% endif %}{% for message in messages %}{% set content = message['content'] %}{% if message['role'] == 'user' %}{{ '<|start_header_id|>user<|end_header_id|>\n\n' + content + '<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\n' }}{% elif message['role'] == 'assistant' %}{{ content + '<|eot_id|>' }}{% endif %}{% endfor %}"
# template = "{{ '<|begin_of_text|>' }}{% if messages[0]['role'] == 'system' %}{% set system_message = messages[0]['content'] %}{% endif %}{% if system_message is defined %}{{ '<|start_header_id|>system<|end_header_id|>\n\n' + system_message + '<|eot_id|>' }}{% endif %}{% for message in messages %}{% set content = message['content'] %}{% if message['role'] == 'user' %}{{ '<|start_header_id|>user<|end_header_id|>\n\n' + content + '<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\n' }}{% elif message['role'] == 'assistant' %}{{ content + '<|eot_id|>' }}{% endif %}{% endfor %}"
template = "{% if messages[0]['role'] == 'system' %}{% set system_message = messages[0]['content'] %}{% endif %}{% if system_message is defined %}{{ system_message + '\n' }}{% endif %}{% for message in messages %}{% set content = message['content'] %}{% if message['role'] == 'user' %}{{ 'Human: ' + content + '\nAssistant:' }}{% elif message['role'] == 'assistant' %}{{ content + '<|end_of_text|>' + '\n' }}{% endif %}{% endfor %}"

# model_name = "Meta-Llama-3.1-8B-Instruct"
# model_name = "Meta-Llama-3.1-8B"
# Create an LLM.
llm = LLM(model=f"{path_dir}")

print(f"model name: {model_name}")
print(f"model_path: {path_dir}")

gen_kwargs_vllm = {
    "max_tokens": 2048,
    "top_p": 1,
    "temperature": 0.0,
    "repetition_penalty": 1.0,
}
tokenizer = llm.get_tokenizer()
if tokenizer.chat_template is None:
    tokenizer.chat_template = template
    tokenizer.chat_template = tokenizer.chat_template.replace("<|eot_id|>", tokenizer.eos_token)
    # tokenizer.chat_template
    gen_kwargs_vllm['stop_token_ids'] = [tokenizer.eos_token_id, tokenizer.convert_tokens_to_ids("<|eot_id|>")]
    print(f"tokenizer.chat_template: {tokenizer.chat_template}")
    print("tokenizer is None, use setted template")
else:
    gen_kwargs_vllm['stop_token_ids'] = [tokenizer.eos_token_id, tokenizer.convert_tokens_to_ids("<|end_of_text|>")]
    print("use original template")
# messages = tokenizer.apply_chat_template(messages, tokenize=False)


sampling_params = SamplingParams(**gen_kwargs_vllm)

# 加载question.jsonl数据集  
questions = datasets.load_dataset('json', data_files='data/arena-hard-v0.1/question.jsonl')['train']  
def convert_to_message(example):  
    messages = [{"role": "user", "content": example["turns"][0]['content']}]  
    example["messages"] = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)  
    return example  
questions = questions.map(convert_to_message)  

# 生成输出  
encoded_inputs = tokenizer.batch_encode_plus(  
    questions['messages'],  
    add_special_tokens=False,
    # padding=True,  # 自动添加padding  
    # truncation=True,  # 如果需要可以截断  
    # return_tensors='pt'  # 返回PyTorch的张量  
) 
input_ids = encoded_inputs['input_ids']  
# outputs = [llm.generate(prompt_token_ids=item, sampling_params=sampling_params)for item in input_ids]
outputs = llm.generate(prompt_token_ids=input_ids, sampling_params=sampling_params)
outputs_text = [x.outputs[0].text for x in outputs]  
token_lens = [len(x.outputs[0].token_ids) for x in outputs]
# 移除现有的 'output' 列并添加新的 'output' 列  
questions = questions.remove_columns(["messages"])  
questions = questions.add_column("output", outputs_text)  
questions = questions.add_column("token_lens", token_lens) 

# 定义转换函数  
def transform_example(example):  
    content = example['output']  
    # tokenized = tokenizer(content)  
    token_len = example['token_lens']   
      
    transformed_example = {  
        "question_id": example['question_id'],  
        "answer_id": example['question_id'],  
        "model_id": model_name,  
        "choices": [  
            {  
                "index": 0,  
                "turns": [  
                    {  
                        "content": content,  
                        "token_len": token_len  
                    }  
                ]  
            }  
        ],  
        # "tstamp": time.time()  
    }  
    return transformed_example  
  
# 对数据集进行转换  
transformed_dataset = questions.map(transform_example, remove_columns=questions.column_names)  
   

/home/v-lingjiang/miniconda3/envs/eval/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-09-20 14:41:58,792	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


WARNING 09-20 14:42:01 arg_utils.py:766] Chunked prefill is enabled by default for models with max_model_len > 32K. Currently, chunked prefill might not work with some features or models. If you encounter any issues, please disable chunked prefill by setting --enable-chunked-prefill=False.
INFO 09-20 14:42:01 config.py:820] Chunked prefill is enabled with max_num_batched_tokens=512.
INFO 09-20 14:42:01 llm_engine.py:174] Initializing an LLM engine (v0.5.4) with config: model='/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/tulu_v2_8b_default_template_dpo_list_bsz1_trible_debug_v14', speculative_config=None, tokenizer='/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/tulu_v2_8b_default_template_dpo_list_bsz1_trible_debug_v14', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, rope_scaling=None, rope_theta=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.bfloat16, max_seq_len=131072, download_dir=None,

Loading safetensors checkpoint shards:   0% Completed | 0/9 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  11% Completed | 1/9 [00:02<00:20,  2.58s/it]
Loading safetensors checkpoint shards:  22% Completed | 2/9 [00:04<00:17,  2.45s/it]
Loading safetensors checkpoint shards:  33% Completed | 3/9 [00:07<00:14,  2.41s/it]
Loading safetensors checkpoint shards:  44% Completed | 4/9 [00:09<00:11,  2.34s/it]
Loading safetensors checkpoint shards:  56% Completed | 5/9 [00:11<00:09,  2.36s/it]
Loading safetensors checkpoint shards:  67% Completed | 6/9 [00:14<00:06,  2.33s/it]
Loading safetensors checkpoint shards:  78% Completed | 7/9 [00:16<00:04,  2.47s/it]
Loading safetensors checkpoint shards:  89% Completed | 8/9 [00:20<00:02,  2.71s/it]
Loading safetensors checkpoint shards: 100% Completed | 9/9 [00:21<00:00,  2.27s/it]
Loading safetensors checkpoint shards: 100% Completed | 9/9 [00:21<00:00,  2.39s/it]


INFO 09-20 14:42:30 model_runner.py:732] Loading model weights took 14.9888 GB


INFO 09-20 14:42:31 gpu_executor.py:102] # GPU blocks: 28232, # CPU blocks: 2048
INFO 09-20 14:42:33 model_runner.py:1024] Capturing the model for CUDA graphs. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 09-20 14:42:33 model_runner.py:1028] CUDA graphs can take additional 1~3 GiB memory per GPU. If you are running out of memory, consider decreasing `gpu_memory_utilization` or enforcing eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INFO 09-20 14:42:44 model_runner.py:1225] Graph capturing finished in 11 secs.
model name: Meta-Llama-3.1-8B-Instruct
model_path: /mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/tulu_v2_8b_default_template_dpo_list_bsz1_trible_debug_v14
use original template


Processed prompts: 100%|██████████| 500/500 [01:45<00:00,  4.75it/s, est. speed input: 473.24 toks/s, output: 2671.98 toks/s]


TypeError: 'RequestOutput' object is not subscriptable

In [8]:
outputs_text = [x.outputs[0].text for x in outputs]  
token_lens = [len(x.outputs[0].token_ids) for x in outputs]
# 移除现有的 'output' 列并添加新的 'output' 列  
# questions = questions.remove_columns(["messages"])  

questions = questions.add_column("output", outputs_text)  
questions = questions.add_column("token_lens", token_lens) 

# 定义转换函数  
def transform_example(example):  
    content = example['output']  
    # tokenized = tokenizer(content)  
    token_len = example['token_lens']   
      
    transformed_example = {  
        "question_id": example['question_id'],  
        "answer_id": example['question_id'],  
        "model_id": model_name,  
        "choices": [  
            {  
                "index": 0,  
                "turns": [  
                    {  
                        "content": content,  
                        "token_len": token_len  
                    }  
                ]  
            }  
        ],  
        # "tstamp": time.time()  
    }  
    return transformed_example  
  
# 对数据集进行转换  
transformed_dataset = questions.map(transform_example, remove_columns=questions.column_names) 

Map: 100%|██████████| 500/500 [00:00<00:00, 15245.47 examples/s]


In [31]:
# gen_kwargs_vllm = {
#     "max_tokens": 2048,
#     "top_p": 1,
#     "temperature": 0.0
# }
# gen_kwargs_vllm['stop_token_ids'] = [tokenizer.eos_token_id, tokenizer.convert_tokens_to_ids("<|end_of_text|>")]
# sampling_params = SamplingParams(**gen_kwargs_vllm)
sampling_params = SamplingParams(n=1, best_of=1, presence_penalty=0.0, frequency_penalty=0.0, repetition_penalty=1.0, temperature=0.0, top_p=1.0, top_k=-1, min_p=0.0, seed=None, use_beam_search=False, length_penalty=1.0, early_stopping=False, stop=[], stop_token_ids=[], include_stop_str_in_output=False, ignore_eos=False, max_tokens=2048, min_tokens=0, logprobs=None, prompt_logprobs=None, skip_special_tokens=True, spaces_between_special_tokens=True, truncate_prompt_tokens=None)
outputs = [llm.generate(prompt_token_ids=item, sampling_params=sampling_params) for item in input_ids[:3]]
outputs_text = [x[0].outputs[0].text for x in outputs]  
token_lens = [len(x[0].outputs[0].token_ids) for x in outputs]
# 移除现有的 'output' 列并添加新的 'output' 列  
# questions = questions.remove_columns(["messages"])  
# questions = questions.remove_columns(['input_ids']) 
# questions = questions.add_column("output", outputs_text)  
# questions = questions.add_column("token_lens", token_lens) 

Processed prompts: 100%|██████████| 1/1 [00:07<00:00,  7.31s/it, est. speed input: 4.10 toks/s, output: 80.27 toks/s]


In [37]:
outputs_text_2 = outputs_text

In [38]:
for i in range(len(outputs_text_1)):
    print(f"{i} {outputs_text_1[i] == outputs_text_2[i]}")

0 True
1 True
2 True


In [43]:
res3 = llm.generate(prompt_token_ids=test_tokens_3, sampling_params=sampling_params)


Processed prompts: 100%|██████████| 1/1 [00:07<00:00,  7.29s/it, est. speed input: 4.11 toks/s, output: 80.48 toks/s]


In [46]:
res3[0].outputs[0].text == origin_data[2]

False

In [42]:
res2[0].outputs[0].text == outputs_text_2[1]

True

In [14]:
questions["messages"][:5]

['Human: Use ABC notation to write a melody in the style of a folk tune.\nAssistant:',
 'Human: SOLVE THIS IN C++ : There are three cards with letters a\n, b\n, c\n placed in a row in some order. You can do the following operation at most once:\n\nPick two cards, and swap them.\nIs it possible that the row becomes abc\n after the operation? Output "YES" if it is possible, and "NO" otherwise.\nInput\nThe first line contains a single integer t\n (1≤t≤6\n) — the number of test cases.\n\nThe only line of each test case contains a single string consisting of each of the three characters a\n, b\n, and c\n exactly once, representing the cards.\n\nOutput\nFor each test case, output "YES" if you can make the row abc\n with at most one operation, or "NO" otherwise.\n\nYou can output the answer in any case (for example, the strings "yEs", "yes", "Yes" and "YES" will be recognized as a positive answer).\n\nExample\ninputCopy\n6\nabc\nacb\nbac\nbca\ncab\ncba\noutputCopy\nYES\nYES\nYES\nNO\nNO\nYES\

In [6]:
outputs_text_1 = outputs_text

In [18]:
origin_data = [data_dict[x] for x in questions["question_id"][:3]]
origin_data

['### Melody in ABC Notation: "The Old Folks at Home"  \n**Title**: The Old Folks at Home  \n**Composer**: Stephen Foster  \n**Key**: G Major  \n**Time Signature**: 4/4  \n**Tempo**: Moderato  \n**Style**: Folk Tune  \n**ABC Notation**:  \n```\nX: 1  \nT: The Old Folks at Home  \nM: 4/4  \nL: 1/4  \nK: G  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G

In [30]:
input_ids[1] == test_tokens_2, input_ids[2] == test_tokens_3, input_ids[0] == test_tokens_1

(True, True, True)

In [29]:
test_tokens_3 = [35075, 25, 83017, 279, 2363, 279, 33365, 3575, 555, 17520, 9052, 13, 40665, 264, 81763, 315, 22100, 323, 6492, 13, 47706, 264, 94798, 315, 5552, 5403, 13, 720, 72803, 25]
test_tokens_1 =  [35075, 25, 5560, 19921, 45297, 311, 3350, 264, 62684, 304, 279, 1742, 315, 264, 29036, 26306, 627, 72803, 25]

In [ ]:
SamplingParams(n=1, best_of=1, presence_penalty=0.0, frequency_penalty=0.0, repetition_penalty=1.0, temperature=0.0, top_p=1.0, top_k=-1, min_p=0.0, seed=None, use_beam_search=False, length_penalty=1.0, early_stopping=False, stop=[], stop_token_ids=[], include_stop_str_in_output=False, ignore_eos=False, max_tokens=2048, min_tokens=0, logprobs=None, prompt_logprobs=None, skip_special_tokens=True, spaces_between_special_tokens=True, truncate_prompt_tokens=None)

In [21]:
test_tokens_2 = [35075, 25, 37023, 4592, 10245, 2006, 356, 1044, 551, 2684, 527, 2380, 7563, 449, 12197, 264, 198, 11, 293, 198, 11, 272, 198, 9277, 304, 264, 2872, 304, 1063, 2015, 13, 1472, 649, 656, 279, 2768, 5784, 520, 1455, 3131, 1473, 38053, 1403, 7563, 11, 323, 14626, 1124, 627, 3957, 433, 3284, 430, 279, 2872, 9221, 40122, 198, 1306, 279, 5784, 30, 9442, 330, 14331, 1, 422, 433, 374, 3284, 11, 323, 330, 9173, 1, 6062, 627, 2566, 198, 791, 1176, 1584, 5727, 264, 3254, 7698, 259, 198, 320, 16, 126863, 83, 126863, 21, 198, 8, 2001, 279, 1396, 315, 1296, 5157, 382, 791, 1193, 1584, 315, 1855, 1296, 1162, 5727, 264, 3254, 925, 31706, 315, 1855, 315, 279, 2380, 5885, 264, 198, 11, 293, 198, 11, 323, 272, 198, 7041, 3131, 11, 14393, 279, 7563, 382, 5207, 198, 2520, 1855, 1296, 1162, 11, 2612, 330, 14331, 1, 422, 499, 649, 1304, 279, 2872, 40122, 198, 449, 520, 1455, 832, 5784, 11, 477, 330, 9173, 1, 6062, 382, 2675, 649, 2612, 279, 4320, 304, 904, 1162, 320, 2000, 3187, 11, 279, 9246, 330, 88, 17812, 498, 330, 9891, 498, 330, 9642, 1, 323, 330, 14331, 1, 690, 387, 15324, 439, 264, 6928, 4320, 3677, 13617, 198, 1379, 12379, 198, 21, 198, 13997, 198, 98571, 198, 56977, 198, 65, 936, 198, 55893, 198, 94929, 198, 3081, 12379, 198, 14331, 198, 14331, 198, 14331, 198, 9173, 198, 9173, 198, 14331, 198, 9290, 198, 644, 279, 1176, 1296, 1162, 11, 584, 1541, 956, 1205, 311, 656, 904, 7677, 11, 2533, 279, 2872, 374, 2736, 40122, 198, 382, 644, 279, 2132, 1296, 1162, 11, 584, 649, 14626, 272, 198, 323, 293, 198, 25, 1645, 65, 52118, 13997, 198, 382, 644, 279, 4948, 1296, 1162, 11, 584, 649, 14626, 293, 198, 323, 264, 198, 25, 80980, 52118, 13997, 198, 382, 644, 279, 11999, 1296, 1162, 11, 433, 374, 12266, 311, 1304, 40122, 198, 1701, 520, 1455, 832, 5784, 627, 72803, 25]

In [39]:
for i in range(len(origin_data)):
    print(f"{i} {origin_data[i] == outputs_text[i]}")

0 True
1 False
2 False


In [33]:
outputs_text

['### Melody in ABC Notation: "The Old Folks at Home"  \n**Title**: The Old Folks at Home  \n**Composer**: Stephen Foster  \n**Key**: G Major  \n**Time Signature**: 4/4  \n**Tempo**: Moderato  \n**Style**: Folk Tune  \n**ABC Notation**:  \n```\nX: 1  \nT: The Old Folks at Home  \nM: 4/4  \nL: 1/4  \nK: G  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G

In [16]:
outputs_text = [x[0].outputs[0].text for x in outputs]  
outputs_text

['### Melody in ABC Notation: "The Old Folks at Home"  \n**Title**: The Old Folks at Home  \n**Composer**: Stephen Foster  \n**Key**: G Major  \n**Time Signature**: 4/4  \n**Tempo**: Moderato  \n**Style**: Folk Tune  \n**ABC Notation**:  \n```\nX: 1  \nT: The Old Folks at Home  \nM: 4/4  \nL: 1/4  \nK: G  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G2 | G2 G2 | G2 G2 | G2 G2 |  \n|: D2 D2 | D2 D2 | D2 D2 | D2 D2 |  \n|: G2 G

In [15]:
import json  
  
def read_jsonl(file_path):  
    """  
    读取 JSONL 文件中的数据并返回一个包含所有记录的字典列表。  
  
    参数:  
    file_path (str): JSONL 文件的路径。  
  
    返回:  
    list: 包含所有记录的字典列表。  
    """  
    data = []  
  
    with open(file_path, 'r', encoding='utf-8') as file:  
        for line in file:  
            # 解析每一行的 JSON 对象并添加到列表中  
            data.append(json.loads(line.strip()))  
  
    return data  
llama_data = read_jsonl("data/arena-hard-v0.1/model_answer/tulu_v2_8b_default_template_dpo_list_bsz1_trible_debug_v14.jsonl")
data_dict = {x["question_id"]: x["choices"][0]["turns"][0]["content"] for x in llama_data}
# data_dict

{'0122ab60646b4961bc39e9c03bdf6bcc': 'Implementing a SCIM (System for Cross-domain Identity Management) server in PHP using Slim as a router involves several steps:\n\n**Step 1: Set up the Slim framework**\n\nFirst, you need to install the Slim framework using Composer:\n\n```bash\ncomposer require slim/slim\n```\n\n**Step 2: Define the SCIM endpoints**\n\nSCIM defines several endpoints for user management, including:\n\n* `GET /Users`: Retrieve a list of users\n* `GET /Users/{id}`: Retrieve a single user by ID\n* `POST /Users`: Create a new user\n* `PATCH /Users/{id}`: Update an existing user\n* `DELETE /Users/{id}`: Delete a user\n\n**Step 3: Implement the SCIM endpoints**\n\nCreate a new PHP file, e.g., `scim.php`, and add the following code to implement the SCIM endpoints:\n```php\n<?php\n\nrequire \'vendor/autoload.php\';\n\nuse Slim\\App;\nuse Slim\\Http\\Request;\nuse Slim\\Http\\Response;\n\n$app = new App();\n\n// Define the SCIM endpoints\n$app->get(\'/Users\', \'getUsers\');

In [13]:
llama_data

[{'question_id': '0122ab60646b4961bc39e9c03bdf6bcc',
  'answer_id': 'HSEj7Ha9GMySp5t9jD787R',
  'model_id': 'Meta-Llama-3.1-8B-Instruct',
  'choices': [{'index': 0,
    'turns': [{'content': 'Implementing a SCIM (System for Cross-domain Identity Management) server in PHP using Slim as a router involves several steps:\n\n**Step 1: Set up the Slim framework**\n\nFirst, you need to install the Slim framework using Composer:\n\n```bash\ncomposer require slim/slim\n```\n\n**Step 2: Define the SCIM endpoints**\n\nSCIM defines several endpoints for user management, including:\n\n* `GET /Users`: Retrieve a list of users\n* `GET /Users/{id}`: Retrieve a single user by ID\n* `POST /Users`: Create a new user\n* `PATCH /Users/{id}`: Update an existing user\n* `DELETE /Users/{id}`: Delete a user\n\n**Step 3: Implement the SCIM endpoints**\n\nCreate a new PHP file, e.g., `scim.php`, and add the following code to implement the SCIM endpoints:\n```php\n<?php\n\nrequire \'vendor/autoload.php\';\n\nuse 

In [3]:
input_ids[:2]

[[128000,
  128006,
  9125,
  128007,
  271,
  38766,
  1303,
  33025,
  2696,
  25,
  6790,
  220,
  2366,
  18,
  198,
  15724,
  2696,
  25,
  220,
  1627,
  10263,
  220,
  2366,
  19,
  271,
  128009,
  128006,
  882,
  128007,
  271,
  10464,
  19921,
  45297,
  311,
  3350,
  264,
  62684,
  304,
  279,
  1742,
  315,
  264,
  29036,
  26306,
  13,
  128009,
  128006,
  78191,
  128007,
  271],
 [128000,
  128006,
  9125,
  128007,
  271,
  38766,
  1303,
  33025,
  2696,
  25,
  6790,
  220,
  2366,
  18,
  198,
  15724,
  2696,
  25,
  220,
  1627,
  10263,
  220,
  2366,
  19,
  271,
  128009,
  128006,
  882,
  128007,
  271,
  50,
  85422,
  10245,
  2006,
  356,
  1044,
  551,
  2684,
  527,
  2380,
  7563,
  449,
  12197,
  264,
  198,
  11,
  293,
  198,
  11,
  272,
  198,
  9277,
  304,
  264,
  2872,
  304,
  1063,
  2015,
  13,
  1472,
  649,
  656,
  279,
  2768,
  5784,
  520,
  1455,
  3131,
  1473,
  38053,
  1403,
  7563,
  11,
  323,
  14626,
  1124,
  627,
  3

In [7]:
outputs = [llm.generate(prompt_token_ids=item, sampling_params=sampling_params) for item in input_ids]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

KeyboardInterrupt: 

In [94]:
res[0].outputs[0].text == original_res[0].outputs[0].text

False

In [77]:
original_res = res


In [78]:
res_batch = res[0].outputs[0].text

In [80]:
res_batch == data

False

In [75]:
res[0].prompt_token_ids == encoded_inputs['input_ids'][0]

True

In [67]:
encoded_inputs['input_ids'][0] == input2

True

In [63]:
res_batch == data

False

In [56]:
len(encoded_inputs['input_ids'][0])

51

In [41]:
with open("res.txt", "r") as f:
    data = f.read()
data == res2

True

In [33]:
input_tokens = tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True) 
print(input_tokens)

<|begin_of_text|><|start_header_id|>system<|end_header_id|>

Cutting Knowledge Date: December 2023
Today Date: 26 Jul 2024

You are a helpful assistant.<|eot_id|><|start_header_id|>user<|end_header_id|>

write pcre regex for not containing  C:<|eot_id|><|start_header_id|>assistant<|end_header_id|>




In [24]:
input2 = [128000, 128006, 9125, 128007, 271, 38766, 1303, 33025, 2696, 25, 6790, 220, 2366, 18, 198, 15724, 2696, 25, 220, 1627, 10263, 220, 2366, 19, 271, 2675, 527, 264, 11190, 18328, 13, 128009, 128006, 882, 128007, 271, 5040, 281, 846, 20791, 369, 539, 8649, 220, 356, 25, 128009, 128006, 78191, 128007, 271]

In [36]:
print(len(input2))

51


In [35]:
prompt = '<|begin_of_text|><|start_header_id|>system<|end_header_id|>\n\nCutting Knowledge Date: December 2023\nToday Date: 26 Jul 2024\n\nYou are a helpful assistant.<|eot_id|><|start_header_id|>user<|end_header_id|>\n\nwrite pcre regex for not containing  C:<|eot_id|><|start_header_id|>assistant<|end_header_id|>\n\n'
encode_prompt = tokenizer.encode(prompt, add_special_tokens=False)
print(len(encode_prompt))

51


In [30]:
with open("prompt_token1.txt", "w") as f:
    f.write(str(input1))

In [27]:
input1 = res[0].prompt_token_ids 

In [15]:
chat_response = client.chat.completions.create(
    model="/mnt/lingjiejiang/textual_aesthetics/model_checkpoint/sft_merge_checkpoints/Meta-Llama-3.1-8B-Instruct",
    messages=[
        {"role": "system", "content": "You are a helpful assistant."},
        {"role": "user", "content": "write pcre regex for not containing  C:"},
    ],
    temperature=0,
    max_tokens=2048
)
# print("Chat response:", chat_response)
print(f"{chat_response.choices[0].message.content}")
res2 = chat_response.choices[0].message.content

To match a string that does not contain 'C:', you can use a negative lookahead assertion in PCRE regex. Here's how you can do it:

```regex
^(?!.*C:).*
```

Explanation:

- `^` asserts the start of the line.
- `(?!` starts a negative lookahead assertion.
- `.*` matches any character (except newline) 0 or more times.
- `C:` is the string we want to avoid.
- `)` ends the negative lookahead assertion.
- `.*` matches any character (except newline) 0 or more times, allowing the regex to match the rest of the string.

However, if you want to match a string that does not contain 'C:' anywhere in the string, not just at the start, you can use the following regex:

```regex
^(?!.*C:).*
```

This will match any string that does not contain 'C:' anywhere in it.

If you want to match a string that does not contain 'C:' at the start, you can use the following regex:

```regex
^(?!C:).*
```

This will match any string that does not start with 'C:'.

Here are some examples in PHP:

```php
$pattern = 

In [16]:
chat_response

ChatCompletion(id='chat-d161e1bd93754f5c88ce9c1a5dbad91a', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='To match a string that does not contain \'C:\', you can use a negative lookahead assertion in PCRE regex. Here\'s how you can do it:\n\n```regex\n^(?!.*C:).*\n```\n\nExplanation:\n\n- `^` asserts the start of the line.\n- `(?!` starts a negative lookahead assertion.\n- `.*` matches any character (except newline) 0 or more times.\n- `C:` is the string we want to avoid.\n- `)` ends the negative lookahead assertion.\n- `.*` matches any character (except newline) 0 or more times, allowing the regex to match the rest of the string.\n\nHowever, if you want to match a string that does not contain \'C:\' anywhere in the string, not just at the start, you can use the following regex:\n\n```regex\n^(?!.*C:).*\n```\n\nThis will match any string that does not contain \'C:\' anywhere in it.\n\nIf you want to match a string that does not cont

In [14]:
with open("res.txt", 'w') as f:
    f.write(res1)

In [12]:
print(res1 == res2)

True
